In [5]:
import random
from IPython.core.display import SVG
import pyomo.environ as pyo
from pysat.solvers import Solver
from pysat.formula import CNF 
import py_svg_combinatorics as psc
from ipywidgets import widgets, HBox
from collections import Counter
from pprint import pprint
from random import randint
import numpy as np
from IPython.display import IFrame
import IPython
from copy import copy
import os
from pathlib import Path
np.set_printoptions(precision=2)
np.set_printoptions(suppress=True)
nbname = ''
try:
    nbname = __vsc_ipynb_file__
except:
    if 'COCALC_JUPYTER_FILENAME' in os.environ:
        nbname = os.environ['COCALC_JUPYTER_FILENAME']    
title_ = Path(nbname).stem.replace('-', '_').title()    
IFrame(f'https://discopal.ispras.ru/index.php?title=Hardprob/{title_}&useskin=cleanmonobook', width=1280, height=300)

Генератор случайных данных


In [6]:
def get_random_m_dim_knapsack(m, n):
    A = np.random.randint(1, 16, size=(m, n))
    c = np.random.randint(1, 1024, size=(n))
    b = np.random.randint(128, 1024, size=(m)) #np.ceil(1/np.random.rand(m))
    return A, b, c

m = np.random.randint(3, 20)
n = np.random.randint(3, 20)

A, b, c = get_random_m_dim_knapsack(m, n)
A, b, c


(array([[ 1,  4, 12,  6, 10,  4, 12,  6,  6,  3,  6],
        [10, 11, 10,  5,  8, 15,  8, 12,  2,  8,  6],
        [ 9,  2, 11,  7,  9,  4, 11,  2,  4,  9,  5],
        [15,  9,  5, 11,  6, 10,  8,  5, 12,  4, 11],
        [11,  2,  1,  9,  5, 12,  4,  1, 10,  8, 11],
        [15,  9,  8, 15,  6,  8,  3, 13,  7, 11,  3],
        [ 3, 11,  7,  8,  3,  8,  4,  6,  3,  1,  4],
        [ 2,  4,  3, 11,  6,  9,  2,  7, 12,  7,  5],
        [11,  4, 13, 13,  3,  9,  8,  7, 10, 12,  5],
        [ 3, 15, 10,  9,  6, 10,  3,  9, 15,  9, 10],
        [ 9,  9,  2, 15, 14,  2,  9,  3, 12,  9,  1],
        [ 7, 11,  3,  6,  7, 12,  1, 14, 14, 10, 15],
        [ 8, 13,  8, 12,  3,  4,  8, 12, 10, 10, 10],
        [ 7, 10,  6, 11, 11, 15, 10,  8,  6, 12,  4],
        [12, 15, 11, 11, 12, 11,  1,  3, 14, 14,  8],
        [15,  5,  6, 10,  4, 11, 14,  3,  6,  5,  8],
        [ 8,  7,  4,  4,  9,  5,  3,  9,  7,  2, 14],
        [ 7,  8,  5,  5,  8, 14,  7, 12, 10, 13, 12],
        [ 2,  4, 14, 12, 10,

In [7]:
def get_model(A, b, c):
    m = pyo.ConcreteModel()

    m.m, m.n = A.shape

    # на всякий случай, возьмем с собой
    m.A = A
    m.b = b
    m.c = c
    
    m.I = range(m.m)
    m.J = range(m.n)
    
    m.x = pyo.Var(m.J, domain=pyo.Binary)
    m.obj = pyo.Objective(expr = sum( c[j] * m.x[j] for j in m.J), sense=pyo.maximize)

    @m.Constraint(m.I)
    def влезает(m, i):
        return sum(A[i, j] * m.x[j] for j in m.J) <= b[i]

    return m

m = get_model(A, b, c)
m.pprint()

2 Set Declarations
    x_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :   11 : {0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10}
    влезает_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :   19 : {0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18}

1 Var Declarations
    x : Size=11, Index=x_index
        Key : Lower : Value : Upper : Fixed : Stale : Domain
          0 :     0 :  None :     1 : False :  True : Binary
          1 :     0 :  None :     1 : False :  True : Binary
          2 :     0 :  None :     1 : False :  True : Binary
          3 :     0 :  None :     1 : False :  True : Binary
          4 :     0 :  None :     1 : False :  True : Binary
          5 :     0 :  None :     1 : False :  True : Binary
          6 :     0 :  None :     1 : False :  True : Binary
          7 :     0 :  None :     1 : False :  True : Bina

In [8]:
solver = pyo.SolverFactory('cbc')
solver.solve(m).write()
m.x.extract_values()

# ==========================================================
# = Solver Results                                         =
# ==========================================================
# ----------------------------------------------------------
#   Problem Information
# ----------------------------------------------------------
Problem: 
- Name: unknown
  Lower bound: 4087.0
  Upper bound: 4087.0
  Number of objectives: 1
  Number of constraints: 0
  Number of variables: 0
  Number of binary variables: 11
  Number of integer variables: 11
  Number of nonzeros: 0
  Sense: maximize
# ----------------------------------------------------------
#   Solver Information
# ----------------------------------------------------------
Solver: 
- Status: ok
  User time: -1.0
  System time: 0.01
  Wallclock time: 0.01
  Termination condition: optimal
  Termination message: Model was solved to optimality (subject to tolerances), and an optimal solution is available.
  Statistics: 
    Branch and bound:

{0: 1.0,
 1: 1.0,
 2: 1.0,
 3: 1.0,
 4: 1.0,
 5: 1.0,
 6: 1.0,
 7: 1.0,
 8: 1.0,
 9: 1.0,
 10: 1.0}